# Electricity consumption
Prediction of Electricity consumption for the first half of 2009

## Imports and reading data

In [19]:
import numpy as np
import pandas as pd
import seaborn as sns
import plotly.express as px
import matplotlib.pyplot as plt
from statsmodels.tsa.seasonal import seasonal_decompose
from statsmodels.tsa.stattools import acf, adfuller
from statsmodels.graphics.tsaplots import plot_acf, plot_pacf

In [20]:
train = pd.read_csv('data/train.csv')
test = pd.read_csv('data/sample.csv')

In [21]:
train

datetime        total
0      01.01.2005 00:00:00          NaN
1      01.01.2005 01:00:00  154139.8084
2      01.01.2005 02:00:00  157818.3593
3      01.01.2005 03:00:00  149310.6991
4      01.01.2005 04:00:00  138282.0380
...                    ...          ...
35059  31.12.2008 19:00:00  249376.3608
35060  31.12.2008 20:00:00  246510.5725
35061  31.12.2008 21:00:00  226469.4133
35062  31.12.2008 22:00:00  199907.3942
35063  31.12.2008 23:00:00  151086.2414

[35064 rows x 2 columns]

#### Missing values

In [22]:
print(train.isna().sum())

datetime      0
total       118
dtype: int64


In [23]:
train.dropna(axis=0, inplace=True)

In [24]:
train.describe()

total
count   34946.000000
mean   185124.542759
std     45576.747296
min     -2683.028891
25%    155648.570400
50%    195441.459350
75%    218380.242775
max    302203.609200

In [25]:

px.box(train, y='total')

Outliers are noticeable, so let's just delete them for now

In [26]:
train[train['total'] < 76000]

datetime         total
2042   27.03.2005 02:00:00   7305.744301
15987  29.10.2006 03:00:00  47898.917280
19514  25.03.2007 02:00:00  -2683.028891
24723  28.10.2007 03:00:00  53230.815110
28417  30.03.2008 01:00:00  58967.138450
28418  30.03.2008 02:00:00  61484.985050
31968  25.08.2008 00:00:00  59079.806790
33459  26.10.2008 03:00:00  39512.542810

In [27]:
px.line(train, y='total', x='datetime')

In [28]:
train = train[train['total'] > 76000]

# Splitting the date into components

In [29]:
tmp = test.copy()

In [30]:
train['datetime'] = pd.to_datetime(train['datetime'], format='%d.%m.%Y %H:%M:%S', dayfirst=True)
tmp['datetime'] = pd.to_datetime(tmp['datetime'], format='%d.%m.%Y %H:%M:%S', dayfirst=True)

C:\Users\user\AppData\Local\Temp\ipykernel_25488\3289478359.py:1: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



In [31]:
train['year'] = train['datetime'].apply(lambda x: x.year)
train['month'] = train['datetime'].apply(lambda x: x.month)
train['hour'] = train['datetime'].apply(lambda x: x.hour)
train['is_summer'] = train['month'].apply(lambda x: x in [6, 7, 8])

tmp['year'] = tmp['datetime'].apply(lambda x: x.year)
tmp['month'] = tmp['datetime'].apply(lambda x: x.month)
tmp['hour'] = tmp['datetime'].apply(lambda x: x.hour)
tmp['is_summer'] = tmp['month'].apply(lambda x: x in [6, 7, 8])

C:\Users\user\AppData\Local\Temp\ipykernel_25488\2221236394.py:1: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

C:\Users\user\AppData\Local\Temp\ipykernel_25488\2221236394.py:2: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

C:\Users\user\AppData\Local\Temp\ipykernel_25488\2221236394.py:3: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-d

In [32]:
train.dropna(inplace=True)
train

C:\Users\user\AppData\Local\Temp\ipykernel_25488\1536476864.py:1: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



datetime        total  year  month  hour  is_summer
1     2005-01-01 01:00:00  154139.8084  2005      1     1      False
2     2005-01-01 02:00:00  157818.3593  2005      1     2      False
3     2005-01-01 03:00:00  149310.6991  2005      1     3      False
4     2005-01-01 04:00:00  138282.0380  2005      1     4      False
5     2005-01-01 05:00:00  132032.7479  2005      1     5      False
...                   ...          ...   ...    ...   ...        ...
35059 2008-12-31 19:00:00  249376.3608  2008     12    19      False
35060 2008-12-31 20:00:00  246510.5725  2008     12    20      False
35061 2008-12-31 21:00:00  226469.4133  2008     12    21      False
35062 2008-12-31 22:00:00  199907.3942  2008     12    22      False
35063 2008-12-31 23:00:00  151086.2414  2008     12    23      False

[34938 rows x 6 columns]

In [33]:
train = pd.get_dummies(train, columns=['month', 'hour'])
tmp = pd.get_dummies(tmp, columns=['month', 'hour'])
train

datetime        total  year  is_summer  month_1  month_2  \
1     2005-01-01 01:00:00  154139.8084  2005      False        1        0   
2     2005-01-01 02:00:00  157818.3593  2005      False        1        0   
3     2005-01-01 03:00:00  149310.6991  2005      False        1        0   
4     2005-01-01 04:00:00  138282.0380  2005      False        1        0   
5     2005-01-01 05:00:00  132032.7479  2005      False        1        0   
...                   ...          ...   ...        ...      ...      ...   
35059 2008-12-31 19:00:00  249376.3608  2008      False        0        0   
35060 2008-12-31 20:00:00  246510.5725  2008      False        0        0   
35061 2008-12-31 21:00:00  226469.4133  2008      False        0        0   
35062 2008-12-31 22:00:00  199907.3942  2008      False        0        0   
35063 2008-12-31 23:00:00  151086.2414  2008      False        0        0   

       month_3  month_4  month_5  month_6  ...  hour_14  hour_15  hour_16  \
1            0        0        0        0  ...        0        0        0   
2            0        0        0        0  ...        0        0        0   
3            0        0        0        0  ...        0        0        0   
4            0        0        0        0  ...        0        0        0   
5            0        0        0        0  ...        0        0        0   
...        ...      ...      ...      ...  ...      ...      ...      ...   
35059        0        0        0        0  ...        0        0        0   
35060        0        0        0        0  ...        0        0        0   
35061        0        0        0        0  ...        0        0        0   
35062        0        0        0        0  ...        0        0        0   
35063        0        0        0        0  ...        0        0        0   

       hour_17  hour_18  hour_19  hour_20  hour_21  hour_22  hour_23  
1            0        0        0        0        0        0        0  
2            0        0        0        0        0        0        0  
3            0        0        0        0        0        0        0  
4            0        0        0        0        0        0        0  
5            0        0        0        0        0        0        0  
...        ...      ...      ...      ...      ...      ...      ...  
35059        0        0        1        0        0        0        0  
35060        0        0        0        1        0        0        0  
35061        0        0        0        0        1        0        0  
35062        0        0        0        0        0        1        0  
35063        0        0        0        0        0        0        1  

[34938 rows x 40 columns]

In [34]:
tmp['month_7'] = 0
tmp['month_8'] = 0
tmp['month_9'] = 0
tmp['month_10'] = 0
tmp['month_11'] = 0
tmp['month_12'] = 0

In [35]:
tmp = tmp[['year', 'is_summer', 'month_1', 'month_2', 'month_3', 'month_4',
       'month_5', 'month_6', 'month_7', 'month_8', 'month_9', 'month_10', 'month_11', 'month_12', 
        'hour_0', 'hour_1', 'hour_2', 'hour_3', 'hour_4',
       'hour_5', 'hour_6', 'hour_7', 'hour_8', 'hour_9', 'hour_10', 'hour_11',
       'hour_12', 'hour_13', 'hour_14', 'hour_15', 'hour_16', 'hour_17',
       'hour_18', 'hour_19', 'hour_20', 'hour_21', 'hour_22', 'hour_23']]
tmp

year  is_summer  month_1  month_2  month_3  month_4  month_5  month_6  \
0     2009      False        1        0        0        0        0        0   
1     2009      False        1        0        0        0        0        0   
2     2009      False        1        0        0        0        0        0   
3     2009      False        1        0        0        0        0        0   
4     2009      False        1        0        0        0        0        0   
...    ...        ...      ...      ...      ...      ...      ...      ...   
4339  2009       True        0        0        0        0        0        1   
4340  2009       True        0        0        0        0        0        1   
4341  2009       True        0        0        0        0        0        1   
4342  2009       True        0        0        0        0        0        1   
4343  2009       True        0        0        0        0        0        1   

      month_7  month_8  ...  hour_14  hour_15  hour_16  hour_17  hour_18  \
0           0        0  ...        0        0        0        0        0   
1           0        0  ...        0        0        0        0        0   
2           0        0  ...        0        0        0        0        0   
3           0        0  ...        0        0        0        0        0   
4           0        0  ...        0        0        0        0        0   
...       ...      ...  ...      ...      ...      ...      ...      ...   
4339        0        0  ...        0        0        0        0        0   
4340        0        0  ...        0        0        0        0        0   
4341        0        0  ...        0        0        0        0        0   
4342        0        0  ...        0        0        0        0        0   
4343        0        0  ...        0        0        0        0        0   

      hour_19  hour_20  hour_21  hour_22  hour_23  
0           0        0        0        0        0  
1           0        0        0        0        0  
2           0        0        0        0        0  
3           0        0        0        0        0  
4           0        0        0        0        0  
...       ...      ...      ...      ...      ...  
4339        1        0        0        0        0  
4340        0        1        0        0        0  
4341        0        0        1        0        0  
4342        0        0        0        1        0  
4343        0        0        0        0        1  

[4344 rows x 38 columns]

## Trainning Model

In [36]:
from sklearn.linear_model import LinearRegression
from sklearn.metrics import r2_score
from sklearn.model_selection import train_test_split

In [37]:
X = train.drop(columns=['datetime', 'total'])
y = train['total']

In [38]:
X_train, X_test, y_train, y_test = train_test_split(X, y, random_state=123, test_size=0.3)
print(X_train.shape)
print(y_train.shape)

(24456, 38)
(24456,)


In [39]:
model = LinearRegression()
model.fit(X_train, y_train)

LinearRegression()

Let's look at the score

In [40]:
answ = model.predict(X_test)
print(r2_score(y_test, answ))

0.8719215763471521


In [41]:
model.coef_

array([ -8098.86926799, -13412.07937695,   3099.18260278,   7275.81122653,
         6682.91280451,   5113.4700301 ,  -7036.68749453,  -2318.92397224,
        -6963.71630409,  -4129.43910062,  -3260.40761484,    217.65905417,
          828.21060102,    491.92816721, -21208.81317371, -54896.7833775 ,
       -71409.0398476 , -79850.81766181, -81176.89121751, -69829.72554482,
       -31341.49656987,  14340.53001919,  25304.90972372,  30067.09105512,
        30879.0327299 ,  28404.24514335,  24056.08575049,  19522.45933799,
        14755.49672498,   9930.62207805,   8585.37407302,   9916.76413891,
        16806.13917995,  27059.14333867,  38252.13917755,  48526.24657685,
        44052.1396584 ,  19255.14868668])

## Predictions

In [42]:
test['total'] = model.predict(tmp)

In [43]:
test

datetime          total
0     01.01.2009 00:00:00  150312.314829
1     01.01.2009 01:00:00  116624.344625
2     01.01.2009 02:00:00  100112.088155
3     01.01.2009 03:00:00   91670.310340
4     01.01.2009 04:00:00   90344.236785
...                   ...            ...
4339  30.06.2009 19:00:00  179750.085389
4340  30.06.2009 20:00:00  190943.081228
4341  30.06.2009 21:00:00  201217.188627
4342  30.06.2009 22:00:00  196743.081709
4343  30.06.2009 23:00:00  171946.090737

[4344 rows x 2 columns]

In [44]:
test.to_csv('Solution.csv', index=False)